## Valuing an Option via the Black–Scholes Model

In [1067]:
import plotly.graph_objects as go
import plotly.express as px
import numpy as np

from plotly.subplots import make_subplots

from typing import NewType
from typing import Literal

In [1068]:
# Define sentinels and consts
NpFloatType = np.float64
OptionType = Literal["call", "put"]
TRADING_DAYS_TO_YEARS = 1 / 252
TRADING_YEARS_TO_DAYS = 252
SEED = 2025

#### Prerequisite Math

The Standard Normal Distribution CDF (where $\sigma = 1$ and $\mu = 0$ ) is given by 

$$\Phi (x) \coloneqq {\frac {1}{2}}\left(1+\operatorname {erf} \left({\frac {x}{\sqrt {2}}}\right)\right)$$

That is $\Phi(z) = \Pr(Z \leq z)$ where $Z \sim \mathcal{N}(\mu = 0, \sigma^2 = 1)$

In [ ]:
# Auxiliary Functions
def erf(x: np.ndarray) -> np.ndarray:
    # from https://www.johndcook.com/blog/python_erf/

    # constants
    a1 = 0.254829592
    a2 = -0.284496736
    a3 = 1.421413741
    a4 = -1.453152027
    a5 = 1.061405429
    p = 0.3275911

    # Abramowitz Stegun formula formula for approxiating erf(x)
    abs_x = np.abs(x)
    t = 1.0 / (1.0 + p * abs_x)
    y = 1.0 - (((((a5 * t + a4) * t) + a3) * t + a2) * t + a1) * t * np.exp(
        -abs_x * abs_x
    )

    return np.sign(x) * y


def std_norm_cdf(x: np.ndarray) -> np.ndarray:
    """
    Returns the cumulative distribution function (CDF) of the standard normal distribution.
    """
    return 0.5 * (1 + erf(x / np.sqrt(2)))


def std_norm_pdf(x: np.ndarray) -> np.ndarray:
    """
    Returns the probability density function (PDF) of the standard normal distribution.
    """
    return np.exp(-0.5 * x**2) / np.sqrt(2 * np.pi)

#### Geometric Brownian Motion


In [1070]:
# plot GMB model for some option
np.random.seed(SEED)
np.random.seed(None)  # Comment this out to get consistent results


def gbm_step(z, mu, sigma, dt):
    """
    One-step multiplicative growth factor in GBM. for z ~ N(0,1)
    """
    return np.exp((mu - 0.5 * sigma * sigma) * dt + sigma * np.sqrt(dt) * z)


# Parameters
initial_stock_price = 100
strike_price = 100
time_to_maturity_years = 0.5
mu = 0.05  # Drift
sigma = 0.2  # Volatility
steps = 256  # Number of time steps we simulate

In [1071]:
def simulate_gbm(
    initial_stock_price, strike_price, mu, sigma, time_to_maturity_years, steps
) -> tuple[np.ndarray, float]:
    step_size = time_to_maturity_years / steps

    # Generate stock path using Geometric Brownian Motion
    standard_normal_shocks = np.random.standard_normal(steps)
    price_path = np.zeros(steps + 1)
    price_path[0] = initial_stock_price
    for t in range(1, steps + 1):
        price_path[t] = price_path[t - 1] * gbm_step(
            standard_normal_shocks[t - 1], mu, sigma, step_size
        )

    # European call option payoff at maturity
    payoff = max(price_path[-1] - strike_price, 0)
    return price_path, payoff


price_path, payoff = simulate_gbm(
    initial_stock_price, strike_price, mu, sigma, time_to_maturity_years, steps
)
payoff

0

In [1072]:
# Plot stock path
fig = go.Figure()
fig.add_trace(go.Scatter(y=price_path, mode="lines", name="Stock Price"))

# Mark buy time (t=0) and expiry (t=T)
fig.add_trace(
    go.Scatter(
        x=[0, steps],
        y=[initial_stock_price, price_path[-1]],
        mode="lines+markers",
        line=dict(dash="dot", color="red"),
        name="Option Buy to Expire",
    )
)

# Add annotation for profit/loss
fig.add_annotation(
    x=steps,
    y=price_path[-1],
    text=f"Payoff={payoff:.2f}",
    showarrow=True,
    arrowhead=4,
)

fig.update_layout(
    title="European Call Option Example (Random Path)",
    xaxis_title="Time (days)",
    yaxis_title="Price",
    template="plotly_dark",
)

fig.show()

#### Black–Scholes Model
We use the [Black–Scholes model](https://en.wikipedia.org/wiki/Black%E2%80%93Scholes_model) to determine the value of a European option given : 

- $r$ - Interest Rate 
- $K$ - Strike Price [Currency] 
- $S$ - Underlying Price [Currency]
- $T$ - Time of option expiration [Years]
- $\sigma$ - Measure of Volatility (square root of the quadratic variation of the stock's log price)  

#### Calculating the Value of Call / Put Options 

Moneyness is the ratio $0 \lt \frac{S}{K} \lt \infty$. For call options if moneyness is $\lt 1$ then we say we are "out of the money" and if its $\gt 1$ we are "in the money".

$d_1$ is a standardized measure of how far the log-moneyness $\ln(S / K)$ may be from zero (i.e. how far it is from breaking even).

$$d_1 = \frac{\ln(S/K) + (r + \tfrac{1}{2}\sigma^2)T}{\sigma \sqrt{T}}$$

$d_2$ shifts $d_1$ down by $\sigma\sqrt{T}$. It represents the standardized moneyness at expiration. 

$$d_2 = d_1 - \sigma \sqrt{T}$$

Using this we express the following for the expected call $C$ and put price $P$ where $\Phi(x)$ is the standard normal distribution. 
$$
C = S \Phi(d_1) - K e^{-rT} \Phi(d_2), \\ \quad \\
P = K e^{-rT} \Phi(-d_2) - S \Phi(-d_1)
$$



In [ ]:
def d1_term(S, K, r, T, sigma):
    return (np.log(S / K) + (r + 0.5 * sigma**2) * T) / (sigma * np.sqrt(T))


def d2_term(S, K, r, T, sigma):
    return d1_term(S, K, r, T, sigma) - sigma * np.sqrt(T)


def black_sholes(
    interest_rate: float,
    strike_price: float,
    underlying_price: np.ndarray,
    time_to_maturity_years: np.ndarray,
    volatility: float,
    option_type: OptionType,
) -> float:
    # Extract the terms
    r = interest_rate
    K = strike_price
    S = underlying_price
    T = time_to_maturity_years  # cast to years
    sigma = volatility

    # Calculate d1 and d2
    d1 = d1_term(S, K, r, T, sigma)
    d2 = d2_term(S, K, r, T, sigma)

    if option_type == "call":
        return S * std_norm_cdf(d1) - K * np.exp(-r * T) * std_norm_cdf(d2)

    if option_type == "put":
        return K * np.exp(-r * T) * std_norm_cdf(-d2) - S * std_norm_cdf(-d1)

    raise ValueError(f"Invalid Option Type `{option_type}`")

#### Heatmaps 

This first plots option prices ($C$ or $P$) against underlying (assest) price (aka spot price $S$) and time to maturity ($T$). 

In [1074]:
# Plot parameters
resolution = 256
epsilon = 1e-5

# Black-Scholes parameters
interest_rate = 0.03
strike_price = 100.0
underlying_price = 80.0
volatility = 0.3
# i.e. moneyness scaled by strike price
spot_prices = np.linspace(0.5, 1, resolution) * strike_price
time_to_maturity_years = np.linspace(epsilon, 5, resolution)

# Meshgrid for spot price and time
XS, YS = np.meshgrid(spot_prices, time_to_maturity_years)

# Compute both surfaces
ZS_call = black_sholes(
    interest_rate=interest_rate,
    strike_price=strike_price,
    underlying_price=XS,
    time_to_maturity_years=YS,
    volatility=volatility,
    option_type="call",
)

ZS_put = black_sholes(
    interest_rate=interest_rate,
    strike_price=strike_price,
    underlying_price=XS,
    time_to_maturity_years=YS,
    volatility=volatility,
    option_type="put",
)

#### Surface Plot of Log Moneyness & Time to Maturity against Option Price

In [1075]:
# Create 1 row × 2 column layout with 3D surface plots
fig = make_subplots(
    rows=1,
    cols=2,
    specs=[[{"type": "surface"}, {"type": "surface"}]],
    subplot_titles=("Call Option Surface", "Put Option Surface"),
    horizontal_spacing=0.05,
    vertical_spacing=0.05,
)

# Add surfaces
log_moneyness = np.log(XS / strike_price)

trace_args = dict(
    x=log_moneyness, y=YS, opacity=0.8, colorscale="plasma", showscale=False
)
fig.add_trace(
    go.Surface(**trace_args, z=ZS_call),
    row=1,
    col=1,
)
fig.add_trace(
    go.Surface(**trace_args, z=ZS_put),
    row=1,
    col=2,
)


# Update axis labels for both scenes
plot_formatting = dict(
    xaxis_title="Log Moneyness (ln(S/K))",
    yaxis_title="Time to Maturity (Years)",
    zaxis_title="Option Price",
    aspectratio=dict(x=1, y=1, z=1),
    xaxis=dict(nticks=4, title_font=dict(size=10), tickfont=dict(size=10)),
    yaxis=dict(nticks=4, title_font=dict(size=10), tickfont=dict(size=10)),
    zaxis=dict(nticks=4, title_font=dict(size=10), tickfont=dict(size=10)),
    camera=dict(eye=dict(x=1.5, y=1.5, z=1.5)),
)

fig.update_layout(
    scene1=plot_formatting,
    scene2=plot_formatting,
    title="Black Scholes Option Surfaces",
    template="plotly_dark",
)

fig.show()

#### Greeks 

Recall the terms 

- $d_1 =\frac{\ln(S/K)+(r+\tfrac{1}{2}\sigma^{2})T}{\sigma\sqrt{T}}$
    - Measures how far the current log-spot price $\ln(S/K)$ is from the strike price. Its adjusts for the risk-free drift and volatility. 
- $d_2 = d_1-\sigma\sqrt{T}$
    - Measures how far the strike is from the distribution of the asset price at expiry (under the risk-neutral measure). $\Phi(d_2)$ gives the probability the option finishes in-the-money.

- $\phi$ Normal Distribution PDF 
- $\Phi$ Normal Distribution CDF


The following terms can be used to better understand an option. We define the terms for European options which have closed form analytical solutions. 

- $\Delta = \frac{\partial \; \cdot}{\partial S} \in [0,1]$ where $\cdot$ is either $C$ or $P$
    - Rate of change of call price with respect to underlying price. Measure sensitivity to underlying price. 
    - $\Delta_\text{call} = \Phi(d_1) \in [0,1]$
    - $\Delta_\text{put} = \Phi(d_1) -1 \in [-1, 0]$

- $\Gamma = \frac{\partial \Delta}{\partial S}$ 
    - Sensitivity of $\Delta$ to underlying price 
    - Curvature of the option price vs spot price (i.e. if $\Gamma \gt 0$ then price vs spot price is locally convex).
    - $\Gamma=\frac{\phi(d_{1})}{S\sigma\sqrt{T}}$


- $\nu = \frac{\partial C}{\partial \sigma}$ 
    - Measure sensitivity to volatility. 
    - Its the change in unit price per change in unit volaility. 
    - $\nu = S\,\phi(d_{1})\sqrt{T}$

- $\Theta = \frac{\partial C}{\partial T}$ 
    - Rate of change of option value with respect to time to maturity (usually negative for calls and puts).
    - $\Theta_{\text{call}} = -\frac{S\phi(d_{1})\sigma}{2\sqrt{T}} - rK e^{-rT}\Phi(d_{2})$
    - $\Theta_{\text{put}} = -\frac{S\phi(d_{1})\sigma}{2\sqrt{T}} + rK e^{-rT}\Phi(-d_{2})$


- $\rho = \frac{\partial C}{\partial r}$ 
    - Measures sensitivity to the interest rate. 
    - $\rho_{\text{call}} = K T e^{-rT}\Phi(d_{2})$
    - $\rho_{\text{put}} = -K T e^{-rT}\Phi(-d_{2})$
    - Most options are not that sensitive to risk-free interest rate $r$ hence its the least used Greek.



We will now plot stock price ($S$) and time to maturity ($T$) against sensitiviy to volatility ($\nu$). 

In [ ]:
# Plot parameters
resolution = 256
epsilon = 1e-5

# Black-Scholes parameters
interest_rate = 0.03
strike_price = 100.0
underlying_price = 80.0
volatility = 0.3
# i.e. moneyness scaled by strike price
spot_prices = np.linspace(0.5, 1, resolution) * strike_price
time_to_maturity_years = np.linspace(epsilon, 5, resolution)

# Meshgrid for spot price and time
XS, YS = np.meshgrid(spot_prices, time_to_maturity_years)


def vega(S, K, r, T, sigma):
    d1 = d1_term(S, K, r, T, sigma)
    return S * std_norm_cdf(d1) * np.sqrt(T)


ZS_vega = vega(XS, strike_price, interest_rate, YS, volatility)

#### Surface Plot of Spot Price & Time to Maturity against Vega

In [1077]:
# Single surface plot of Vega vs Spot Price and Time to Maturity
fig = go.Figure(
    data=[
        go.Surface(
            x=XS,
            y=YS,
            z=ZS_vega,
            opacity=0.8,
            colorscale="plasma",
            showscale=True,
        )
    ]
)

fig.update_layout(
    title="Vega Surface (Black-Scholes)",
    scene=dict(
        xaxis_title="Spot Price (S)",
        yaxis_title="Time to Maturity (Years)",
        zaxis_title="Vega",
        aspectratio=dict(x=1, y=1, z=1),
        xaxis=dict(nticks=4, title_font=dict(size=10), tickfont=dict(size=10)),
        yaxis=dict(nticks=4, title_font=dict(size=10), tickfont=dict(size=10)),
        zaxis=dict(nticks=4, title_font=dict(size=10), tickfont=dict(size=10)),
        camera=dict(eye=dict(x=1.5, y=1.5, z=1.5)),
    ),
    template="plotly_dark",
)

fig.show()